In [18]:
import pandas as pd
import numpy as np
# # set up dictionaries of parameter options for each learner
param_opts = {
    'DecisionTreeClassifier': {},
    'GradientBoostingClassifier': {},
    'KNeighborsClassifier': {},
    'LogisticRegression': {},
    'RandomForestClassifier': {},
    'SVC': {}
}
ml_p = pd.read_csv('ml_p_options.csv')
ml_p.rename(columns={'alg_name':'classifier'},inplace=True)
for ml, df_ml in ml_p.groupby('classifier'):
    for p, df_ml_p in df_ml.groupby('parameters'):
        d = eval(p)
        for keys,v in d.items():
            if keys not in param_opts[ml].keys():
                param_opts[ml][keys] = [v]
            elif v not in param_opts[ml][keys]:
                param_opts[ml][keys].append(v)
print(param_opts)

{'DecisionTreeClassifier': {'criterion': ['entropy', 'gini'], 'max_depth': [2, 4, 6, 8], 'min_samples_leaf': [10, 20, 5], 'min_samples_split': [10, 20, 5]}, 'GradientBoostingClassifier': {'learning_rate': [0.01, 0.1, 1], 'max_depth': [1, 10, 5], 'max_features': ['log2', 'sqrt'], 'min_samples_leaf': [10, 20, 5], 'min_samples_split': [10, 20, 5], 'n_estimators': [100, 250], 'subsample': [0.5, 1]}, 'KNeighborsClassifier': {'n_neighbors': [1, 11, 3, 5, 7, 9], 'p': [1, 2], 'weights': ['distance', 'uniform']}, 'LogisticRegression': {'C': [0.0001, 0.001, 0.01, 0.1, 0.5, 1, 10, 25], 'dual': ['false', 'true'], 'penalty': ['l1', 'l2']}, 'RandomForestClassifier': {'bootstrap': ['false', 'true'], 'criterion': ['entropy', 'gini'], 'max_features': ['log2', 'sqrt'], 'min_samples_leaf': [10, 20, 5], 'min_samples_split': [10, 20, 5], 'n_estimators': [100, 250]}, 'SVC': {'C': [0.0001, 0.001, 0.01, 0.1, 0.5, 1, 10, 25], 'kernel': ['poly', 'rbf'], 'tol': [0.0001, 0.001, 0.01, 0.1, 1e-05]}}


In [19]:
import pandas as pd
import numpy as np

data = pd.read_csv('sklearn-benchmark5-data-edited.tsv.gz', sep='\t', names=['dataset',
                                                                     'classifier',
                                                                     'parameters',
                                                                     'accuracy', 
                                                                     'macrof1',
                                                                     'bal_accuracy']).fillna('')
print(data.head())
data['accuracy'] = data['accuracy'].apply(lambda x: round(x, 3))
print('loaded ',data['dataset'].unique().shape[0],'datasets and ', data['classifier'].unique().shape[0],'classifiers')
# subset data to classifiers used in PennAI
pennai_classifiers = ['LogisticRegression', 'RandomForestClassifier', 'SVC', 
                      'KNeighborsClassifier', 'DecisionTreeClassifier', 'GradientBoostingClassifier']
mask = np.array([c in pennai_classifiers for c in data['classifier'].values])
data = data.loc[mask,:]
print('datasets (',len(data['dataset'].unique()),')')
print('classifiers (',len(data['classifier'].unique()),'):',data['classifier'].unique())
for ml, df_g in data.groupby('classifier'):
    print('parameters for ',ml,'(',len(df_g['parameters'].unique()),'):',df_g['parameters'].unique()[:5])


/home/bill/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (5) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


                                             dataset          classifier  \
0  GAMETES_Epistasis_2-Way_1000atts_0.4H_EDM-1_ED...  AdaBoostClassifier   
1  GAMETES_Epistasis_2-Way_1000atts_0.4H_EDM-1_ED...  AdaBoostClassifier   
2  GAMETES_Epistasis_2-Way_1000atts_0.4H_EDM-1_ED...  AdaBoostClassifier   
3  GAMETES_Epistasis_2-Way_1000atts_0.4H_EDM-1_ED...  AdaBoostClassifier   
4  GAMETES_Epistasis_2-Way_1000atts_0.4H_EDM-1_ED...  AdaBoostClassifier   

                             parameters  accuracy   macrof1 bal_accuracy  
0    learning_rate=0.01,n_estimators=10  0.479375  0.470857   0.479375.1  
1   learning_rate=0.01,n_estimators=100  0.476875  0.476497     0.476875  
2  learning_rate=0.01,n_estimators=1000  0.488125  0.488115     0.488125  
3    learning_rate=0.01,n_estimators=50  0.483750  0.483652      0.48375  
4   learning_rate=0.01,n_estimators=500  0.495625  0.495609     0.495625  
loaded  166 datasets and  13 classifiers
datasets ( 166 )
classifiers ( 6 ): ['DecisionTreeCl

In [20]:
from collections import OrderedDict

def convert_params(params):
    """convert from sklearn-style parameter formatting to dictionary, PennAI style."""
    pdict = {}
    for kv in params.split(','):
        if len(kv)==0: continue
#         print(kv.split('='))
        pdict[str(kv.split('=')[0])] = kv.split('=')[1]
    for k,v in pdict.items():
        try:
            pdict[k] = int(v)
        except ValueError:
            try:     
                pdict[k] = float(v)
            except ValueError:
                pass

    return OrderedDict(sorted(pdict.items()))


data['parameters'] = data['parameters'].apply(lambda x: convert_params(x))

In [4]:
for ml, df_g in data.groupby('classifier'):
    print('example parameters for ',ml,'(',len(df_g['parameters'].apply(str).unique()),'):',
           df_g['parameters'].apply(str).unique()[0])

example parameters for  DecisionTreeClassifier ( 154 ): OrderedDict([('criterion', 'entropy'), ('max_features', 0.1), ('min_weight_fraction_leaf', 0.0)])
example parameters for  GradientBoostingClassifier ( 6301 ): OrderedDict([('learning_rate', 0.01), ('loss', 'deviance'), ('max_depth', 1), ('max_features', 0.2), ('n_estimators', 10)])
example parameters for  KNeighborsClassifier ( 54 ): OrderedDict([('n_neighbors', 1), ('weights', 'distance')])
example parameters for  LogisticRegression ( 240 ): OrderedDict([('C', 0.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')])
example parameters for  RandomForestClassifier ( 770 ): OrderedDict([('criterion', 'entropy'), ('max_features', 0.1), ('min_weight_fraction_leaf', 0.0), ('n_estimators', 10)])
example parameters for  SVC ( 1239 ): OrderedDict([('C', 0.01), ('coef0', 0.0), ('degree', 2), ('gamma', 0.01), ('kernel', 'poly')])


In [17]:
def valid_param_combo(ml,params):
#     print('ml',ml,type(ml).__name__)
#     print('params',params,type(params).__name__)

    for k,v in params.items():
        if k in param_opts[ml].keys():
            if param_opts[ml][k] is int:
                try:
                    if int(v) in param_opts[ml][k]:
                        return True
                except: 
                    return False
            elif param_opts[ml][k] is float:
                try:
                    if float(v) in param_opts[ml][k]:
                        return True
                except: 
                    return False
            elif v not in param_opts[ml][k]:
#                 if ml == 'LogisticRegression' and k=='C':
#                     print('eliminating',params,'for',ml,'with',k,':',v)
                    return False
    return True

mask = [valid_param_combo(row['classifier'],row['parameters']) for _, row in data.iterrows()]
mask = mask | data.classifier=='LogisticRegression'
data_filtered = data.loc[mask]

# data_filtered = data.loc[lambda x: valid_param_combo(i['classifier'],i['parameters']) for i in x]


eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 10.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 10.5
eliminating OrderedDict

eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 10.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 10.5
eliminating OrderedDict

eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 10.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 10.5
eliminating OrderedDict

eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 10.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 10.5
eliminating OrderedDict

eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 10.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 10.5
eliminating OrderedDict

...

eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 10.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 10.5
eliminating OrderedDict

eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 10.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 10.5
eliminating OrderedDict([('C', 10.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l1')]) for LogisticRegression with C : 10.5
eliminating OrderedDic

eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l1')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 1.5), ('dual', 'True'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 1.5
eliminating OrderedDict([('C', 10.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 10.5
eliminating OrderedDict

eliminating OrderedDict([('C', 9.0), ('dual', 'True'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 9.0
eliminating OrderedDict([('C', 9.0), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 9.0
eliminating OrderedDict([('C', 9.0), ('dual', 'True'), ('fit_intercept', 'True'), ('penalty', 'l2')]) for LogisticRegression with C : 9.0
eliminating OrderedDict([('C', 9.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')]) for LogisticRegression with C : 9.5
eliminating OrderedDict([('C', 9.5), ('dual', 'False'), ('fit_intercept', 'True'), ('penalty', 'l1')]) for LogisticRegression with C : 9.5
eliminating OrderedDict([('C', 9.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 9.5
eliminating OrderedDict([('C', 9.5), ('dual', 'True'), ('fit_intercept', 'False'), ('penalty', 'l2')]) for LogisticRegression with C : 9.5
eliminating OrderedDict([(

TypeError: unsupported operand type(s) for |: 'bool' and 'str'

In [21]:
for ml, df_g in data_filtered.groupby('classifier'):
    print('example parameters for ',ml,'(',len(df_g['parameters'].apply(str).unique()),'):',
           df_g['parameters'].apply(str).unique()[0])

example parameters for  DecisionTreeClassifier ( 154 ): OrderedDict([('criterion', 'entropy'), ('max_features', 0.1), ('min_weight_fraction_leaf', 0.0)])
example parameters for  GradientBoostingClassifier ( 6301 ): OrderedDict([('learning_rate', 0.01), ('loss', 'deviance'), ('max_depth', 1), ('max_features', 0.2), ('n_estimators', 10)])
example parameters for  KNeighborsClassifier ( 54 ): OrderedDict([('n_neighbors', 1), ('weights', 'distance')])
example parameters for  LogisticRegression ( 18 ): OrderedDict([('C', 0.5), ('dual', 'False'), ('fit_intercept', 'False'), ('penalty', 'l1')])
example parameters for  RandomForestClassifier ( 770 ): OrderedDict([('criterion', 'entropy'), ('max_features', 0.1), ('min_weight_fraction_leaf', 0.0), ('n_estimators', 10)])
example parameters for  SVC ( 1239 ): OrderedDict([('C', 0.01), ('coef0', 0.0), ('degree', 2), ('gamma', 0.01), ('kernel', 'poly')])


In [22]:
param_opts['LogisticRegression']

{'C': [0.0001, 0.001, 0.01, 0.1, 0.5, 1, 10, 25],
 'dual': ['false', 'true'],
 'penalty': ['l1', 'l2']}

In [23]:
print(data[data['classifier']=='KNeighborsClassifier']['parameters'].apply(str).unique())

["OrderedDict([('n_neighbors', 1), ('weights', 'distance')])"
 "OrderedDict([('n_neighbors', 1), ('weights', 'uniform')])"
 "OrderedDict([('n_neighbors', 10), ('weights', 'distance')])"
 "OrderedDict([('n_neighbors', 10), ('weights', 'uniform')])"
 "OrderedDict([('n_neighbors', 100), ('weights', 'distance')])"
 "OrderedDict([('n_neighbors', 100), ('weights', 'uniform')])"
 "OrderedDict([('n_neighbors', 11), ('weights', 'distance')])"
 "OrderedDict([('n_neighbors', 11), ('weights', 'uniform')])"
 "OrderedDict([('n_neighbors', 12), ('weights', 'distance')])"
 "OrderedDict([('n_neighbors', 12), ('weights', 'uniform')])"
 "OrderedDict([('n_neighbors', 13), ('weights', 'distance')])"
 "OrderedDict([('n_neighbors', 13), ('weights', 'uniform')])"
 "OrderedDict([('n_neighbors', 14), ('weights', 'distance')])"
 "OrderedDict([('n_neighbors', 14), ('weights', 'uniform')])"
 "OrderedDict([('n_neighbors', 15), ('weights', 'distance')])"
 "OrderedDict([('n_neighbors', 15), ('weights', 'uniform')])"


In [24]:
data_filtered.head()

dataset  \
175  GAMETES_Epistasis_2-Way_1000atts_0.4H_EDM-1_ED...   
176  GAMETES_Epistasis_2-Way_1000atts_0.4H_EDM-1_ED...   
177  GAMETES_Epistasis_2-Way_1000atts_0.4H_EDM-1_ED...   
178  GAMETES_Epistasis_2-Way_1000atts_0.4H_EDM-1_ED...   
179  GAMETES_Epistasis_2-Way_1000atts_0.4H_EDM-1_ED...   

                 classifier  \
175  DecisionTreeClassifier   
176  DecisionTreeClassifier   
177  DecisionTreeClassifier   
178  DecisionTreeClassifier   
179  DecisionTreeClassifier   

                                            parameters  accuracy   macrof1  \
175  {'criterion': 'entropy', 'max_features': 0.1, ...     0.507  0.507488   
176  {'criterion': 'gini', 'max_features': 0.1, 'mi...     0.476  0.476040   
177  {'criterion': 'entropy', 'max_features': 0.25,...     0.507  0.506832   
178  {'criterion': 'gini', 'max_features': 0.25, 'm...     0.490  0.489993   
179  {'criterion': 'entropy', 'max_features': 0.5, ...     0.512  0.512497   

    bal_accuracy  
175       0.5075  
176      0.47625  
177     0.506875  
178         0.49  
179       0.5125

In [65]:
print('data_filtered shape: ', data_filtered.shape)
print('datasets (',len(data_filtered['dataset'].unique()),')')
print('classifiers (',len(data_filtered['classifier'].unique()),'):',data_filtered['classifier'].unique())
for ml, df_g in data_filtered.groupby('classifier'):
    print('parameters for ',ml,'(',len(df_g['parameters'].apply(str).unique()),'):',
           df_g['parameters'].apply(str).unique()[:5])

data_filtered shape:  (113740, 6)
datasets ( 165 )
classifiers ( 5 ): ['DecisionTreeClassifier' 'GradientBoostingClassifier'
 'KNeighborsClassifier' 'RandomForestClassifier' 'SVC']
parameters for  DecisionTreeClassifier ( 154 ): ["OrderedDict([('criterion', 'entropy'), ('max_features', 0.1), ('min_weight_fraction_leaf', 0.0)])"
 "OrderedDict([('criterion', 'gini'), ('max_features', 0.1), ('min_weight_fraction_leaf', 0.0)])"
 "OrderedDict([('criterion', 'entropy'), ('max_features', 0.25), ('min_weight_fraction_leaf', 0.0)])"
 "OrderedDict([('criterion', 'gini'), ('max_features', 0.25), ('min_weight_fraction_leaf', 0.0)])"
 "OrderedDict([('criterion', 'entropy'), ('max_features', 0.5), ('min_weight_fraction_leaf', 0.0)])"]
parameters for  GradientBoostingClassifier ( 36 ): ["OrderedDict([('learning_rate', 0.01), ('loss', 'deviance'), ('max_depth', 1), ('max_features', 'log2'), ('n_estimators', 100)])"
 "OrderedDict([('learning_rate', 0.01), ('loss', 'deviance'), ('max_depth', 1), ('max_f

In [65]:
print('data_filtered shape: ', data_filtered.shape)
print('datasets (',len(data_filtered['dataset'].unique()),')')
print('classifiers (',len(data_filtered['classifier'].unique()),'):',data_filtered['classifier'].unique())
for ml, df_g in data_filtered.groupby('classifier'):
    print('parameters for ',ml,'(',len(df_g['parameters'].apply(str).unique()),'):',
           df_g['parameters'].apply(str).unique()[:5])

data_filtered shape:  (113740, 6)
datasets ( 165 )
classifiers ( 5 ): ['DecisionTreeClassifier' 'GradientBoostingClassifier'
 'KNeighborsClassifier' 'RandomForestClassifier' 'SVC']
parameters for  DecisionTreeClassifier ( 154 ): ["OrderedDict([('criterion', 'entropy'), ('max_features', 0.1), ('min_weight_fraction_leaf', 0.0)])"
 "OrderedDict([('criterion', 'gini'), ('max_features', 0.1), ('min_weight_fraction_leaf', 0.0)])"
 "OrderedDict([('criterion', 'entropy'), ('max_features', 0.25), ('min_weight_fraction_leaf', 0.0)])"
 "OrderedDict([('criterion', 'gini'), ('max_features', 0.25), ('min_weight_fraction_leaf', 0.0)])"
 "OrderedDict([('criterion', 'entropy'), ('max_features', 0.5), ('min_weight_fraction_leaf', 0.0)])"]
parameters for  GradientBoostingClassifier ( 36 ): ["OrderedDict([('learning_rate', 0.01), ('loss', 'deviance'), ('max_depth', 1), ('max_features', 'log2'), ('n_estimators', 100)])"
 "OrderedDict([('learning_rate', 0.01), ('loss', 'deviance'), ('max_depth', 1), ('max_f

# remove big datasets

In [25]:
data_filtered = data
#datasets to remove:
big_datasets = ['poker', 'kddcup', 'sleep', 'fars', 'mnist', 'connect-4', 'shuttle', 'adult', 'krkopt', 
                'letter', 'magic', 'nursery', 'pendigits', 'coil2000', 'agaricus-lepiota','optdigits']
mask = np.array([d not in big_datasets for d in data_filtered['dataset'].values])
clean_data = data_filtered.loc[mask,:]
clean_data.groupby('dataset').count()
print(len(clean_data['dataset'].unique()),'datasets left')

150 datasets left


# remove alg-params that don't cover all datasets

In [26]:
clean_data.loc[:, 'algorithm-parameters'] = (                                             
                                       clean_data['classifier'].values + '|' +                     
                                       clean_data['parameters'].apply(str).values) 
all_datasets = np.unique(clean_data['dataset'].values)
algp_toremove = []
for algp, group in clean_data.groupby('algorithm-parameters'):
    if (group['dataset'].count()<150):
        #print(algp, '\n\t is missing results for', [d for d in all_datasets if d not in np.unique(group['dataset'])])
        #print('removing',algp)
        algp_toremove.append(algp)
        
mask = np.array([ap not in algp_toremove for ap in clean_data['algorithm-parameters'].values])
print('removing',np.sum(~mask),'algorithm-parameter combinations')
clean_data = clean_data.loc[mask,:]
print('new size:',len(clean_data))
clean_data.drop('algorithm-parameters',axis=1,inplace=True)

clean_data.groupby('classifier').count()

/home/bill/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:362: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
/home/bill/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


removing 557240 algorithm-parameter combinations
new size: 513450


dataset  parameters  accuracy  macrof1  \
classifier                                                           
DecisionTreeClassifier        23100       23100     23100    23100   
GradientBoostingClassifier   329700      329700    329700   329700   
KNeighborsClassifier           7500        7500      7500     7500   
LogisticRegression            36000       36000     36000    36000   
RandomForestClassifier       115500      115500    115500   115500   
SVC                            1650        1650      1650     1650   

                            bal_accuracy  
classifier                                
DecisionTreeClassifier             23100  
GradientBoostingClassifier        329700  
KNeighborsClassifier                7500  
LogisticRegression                 36000  
RandomForestClassifier            115500  
SVC                                 1650

# write modified data to file

In [27]:
clean_data.to_csv('sklearn-benchmark5-data-mock_experiment.tsv.gz',compression='gzip',index=False,sep='\t',
                  header=['dataset',
                                 'algorithm',
                                 'parameters',
                                 'accuracy', 
                                 'macrof1',
                                 'bal_accuracy'])